In [ ]:
import pfv_utils.utils as pu
import vision.data.proto.annotated_image_pb2
import vision.data.proto.oriented_bounding_box_annotation_extension_pb2
import vision.data.tools.fiducial_annotator.fiducial_annotator_pb2
import tensorflow as tf
import numpy as np
import os

In [ ]:
tf.reshape

In [ ]:
reload(pu)

In [ ]:
pu.test_create_extents_loss()

In [ ]:
pu.test_create_fiducials_loss_log_var()

In [ ]:
assert [None] == [None]

In [ ]:
def is_valid_length(l):
    return l > 1 and l < 23

In [ ]:
# Path to extents data.
#extents_lmdbs_dir = '/home/praveen/data//scale/extent_regression_training_data2/train/'
#extents_lmdbs_dir = '/mnt/nautilus_rw/praveen/pfv/scale_extent_new_training_batches/'
extents_lmdbs_dir = '/home/praveen/data/scale_extent_new_training_batches/'
extents_lmdb_paths = pu.get_sorted_lmdb_paths_in_dir(extents_lmdbs_dir)
extents_lmdb_paths = filter(lambda x: is_valid_length(int(os.path.basename(x).replace('.lmdb', ''))) 
                            , extents_lmdb_paths)
#extents_lmdb_paths = filter(lambda x: '1' not in x and '22' not in x, extents_lmdb_paths)

In [ ]:
len(extents_lmdb_paths)

In [ ]:
# Path to fiducials data.
#fiducial_lmdbs_dir = '/mnt/nautilus_rw/praveen/big_fiducials_dataset_joined_20_split/train/'
#fiducial_lmdbs_dir = '/home/praveen/data/big_fiducials_dataset_joined_20/'
#fiducial_lmdbs_dir = '/mnt/nautilus_rw/praveen/wheel_road_ais/small_joined/'
fiducial_lmdbs_dir = '/home/praveen/data/big_fiducials_dataset_joined_20_split/train/'
c1r_fiducials_lmdbs_dir = '/home/praveen/data/pfv/2018/10/19/c1r_fiducials_dataset/train/'
fiducial_lmdbs_paths = pu.get_sorted_lmdb_paths_in_dir(fiducial_lmdbs_dir) + pu.get_sorted_lmdb_paths_in_dir(c1r_fiducials_lmdbs_dir)

In [ ]:
len(fiducial_lmdbs_paths)

In [ ]:
extent_lmdbs = [pu.LMDBIterator(f) for f in extents_lmdb_paths]

In [ ]:
fiducial_lmdbs = [pu.LMDBIterator(f) for f in fiducial_lmdbs_paths]

In [ ]:
fiducials_ai = vision.data.proto.annotated_image_pb2.AnnotatedImage()
fiducials_ai.ParseFromString(fiducial_lmdbs[0].kv_pair[1])

In [ ]:
pu.get_fids_from_ai(fiducials_ai)

In [ ]:
fiducials_ai.groundtruth[0].Extensions[vision.data.tools.fiducial_annotator.fiducial_annotator_pb2.FiducialsAnnotation.ext].fiducial[0]

In [ ]:
extents_ai = vision.data.proto.annotated_image_pb2.AnnotatedImage()
extents_ai.ParseFromString(extent_lmdbs[0].kv_pair[1])

In [ ]:
import matplotlib.pyplot as plt

In [ ]:
%matplotlib inline

In [ ]:
batch_size = 1

In [ ]:
fiducials_keys = ['wheel_back_left', 'wheel_back_right', 'wheel_front_left', 'wheel_front_right']

In [ ]:
import time

In [ ]:
reload(pu)

In [ ]:
net = pu.VehicleGeometryNet(1,1,1)#.2,2.5,.1)

In [ ]:
train_step = tf.train.AdamOptimizer(1e-4).minimize(net.loss)

In [ ]:
config = tf.ConfigProto()
config.gpu_options.allow_growth = True
sess = tf.Session(config=config)
sess.run(tf.global_variables_initializer())
iter = 0


In [ ]:
#output_dir = '/mnt/nautilus_rw/praveen/pfv/2018/08/21/all_vars/'
output_dir = '/mnt/nautilus_rw/praveen/pfv/2018/10/19/all_vars/'
try:
    os.makedirs(output_dir)
except:
    pass

In [ ]:
def serialize_graph_to_file(sess, output_dir, filename):
    graphdef = sess.graph_def
    output_node_names = ['fiducials_vis_output', 'fiducials_xy_output',
                                                                            'extents_output', 
                         'extents_log_vars_output', 'fiducials_xy_log_vars_output']
    
    #output_node_names[0] = "fiducials_vis_logits"
    #output_node_names = output_node_names[1:]
    frozen_graph = tf.graph_util.convert_variables_to_constants(sess, graphdef, output_node_names) 
    #frozen_graph = tf.graph_util.remove_training_nodes(frozen_graph)
    #frozen_graph = tf.graph_util.extract_sub_graph(frozen_graph, output_node_names)
    tf.train.write_graph(frozen_graph, output_dir, filename, as_text=False)
    print 'Wrote to: ' + output_dir + '/' + filename


In [ ]:
all_losses = []

In [ ]:
while iter < 1000001:
    start = time.time()
    # Compose batch from extent_lmdbs.
    batch_ims = []
    full_batch_size = batch_size* (len(extent_lmdbs)+ len(fiducial_lmdbs))
    batch_extents_gts = np.zeros(pu.get_size_for_batch(net.extents_gt.shape, full_batch_size))
    batch_extents_loss_mask = np.zeros(pu.get_size_for_batch(net.extents_loss_mask.shape, full_batch_size))
    
    batch_fiducials_xy = np.zeros(pu.get_size_for_batch(net.fiducials_xy_gt.shape, full_batch_size))
    batch_fiducials_xy_loss_mask = np.zeros(pu.get_size_for_batch(net.fiducials_xy_loss_mask.shape, full_batch_size))
    batch_fiducials_vis = np.zeros(pu.get_size_for_batch(net.fiducials_vis_gt.shape, full_batch_size))
    batch_fiducials_vis_loss_mask = np.zeros(pu.get_size_for_batch(net.fiducials_vis_loss_mask.shape, 
                                                                   full_batch_size))
    
    batch_item_idx = -1
    for extent_lmdb in extent_lmdbs:
        for i in range(0,batch_size):
            batch_item_idx +=1
            ai = vision.data.proto.annotated_image_pb2.AnnotatedImage()
            ai.ParseFromString(extent_lmdb.kv_pair[1])
            extent_lmdb.next()
            
            batch_ims.append(pu.get_image_from_ai(ai))
            batch_extents_gts[batch_item_idx,:] = pu.get_extents_from_ai(ai)
            batch_extents_loss_mask[batch_item_idx] = 1
    
    fid_ais = []
    for fiducial_lmdb in fiducial_lmdbs:
        for i in range(0,batch_size):
            batch_item_idx +=1
            ai = vision.data.proto.annotated_image_pb2.AnnotatedImage()
            ai.ParseFromString(fiducial_lmdb.kv_pair[1])
            fiducial_lmdb.next()            
            batch_ims.append(pu.get_image_from_ai(ai))
            fid_ais.append(ai)
            
            fiducials_dict = pu.get_fids_from_ai(ai)
            batch_fiducials_vis_loss_mask[batch_item_idx] = 1

            for fid_idx, fid_key in enumerate(fiducials_keys):
                fid_data = np.array(fiducials_dict[fid_key])
                batch_fiducials_xy[batch_item_idx,fid_idx,:] = fid_data[0:2]
                vis =  (fid_data[2] > 0) and  np.all(fid_data[0:2] >0) and np.all(fid_data[0:2] < 64)
                batch_fiducials_xy_loss_mask[batch_item_idx,fid_idx] = vis
                batch_fiducials_vis[batch_item_idx,fid_idx] = vis and (fid_data[2] ==1)
            
                
    end = time.time()

    normalized_batch_ims = pu.normalize_ims(np.array(batch_ims))
    batch_fiducials_xy = (batch_fiducials_xy - 32.0) / 64.0
    
    step_start = time.time()
    loss, fid_loss, fid_vis_loss, ext_loss,batch_extents_log_vars_output,_ = sess.run([net.loss, 
                                                                                         net.fiducials_loss, 
                                                                                         net.fiducials_vis_loss, 
                                                                                         net.extents_loss, 
                                                                                         net.extents_log_vars_output, train_step], feed_dict={net.x: normalized_batch_ims,
                                          net.extents_gt: batch_extents_gts, 
                                           net.extents_loss_mask: batch_extents_loss_mask,
                                                              net.fiducials_xy_gt: batch_fiducials_xy,
                                                               net.fiducials_xy_loss_mask: batch_fiducials_xy_loss_mask,
                                                                net.fiducials_vis_gt: batch_fiducials_vis,
                                                                net.fiducials_vis_loss_mask: batch_fiducials_vis_loss_mask})
    
    all_losses.append((loss, fid_loss,fid_vis_loss, ext_loss))
    if iter % 200 == 0:
        last_fiducials_xy_loss_mask = batch_fiducials_xy_loss_mask.copy()
        last_batch_ims = list(batch_ims)
        last_batch_fid_xy = batch_fiducials_xy.copy()
        last_batch_fid_loss = fid_loss
        last_batch_fid_ais = list(fid_ais)
        last_batch_extents_gts = batch_extents_gts
        print 'On iter: %d; loss: %0.2f\t fid loss: %0.2f\t ext loss: %0.2f\t fid_vis loss: %0.2f' % (iter, loss,
                                                                                fid_loss, ext_loss, fid_vis_loss)

    step_end = time.time()
    
    if iter % 20000 == 0:
        serialize_graph_to_file(sess, output_dir, '%08d.pb' % iter)
            
    iter+=1
    

In [ ]:
net.fiducials_vis_output

In [ ]:
batch_fiducials_xy.shape

In [ ]:
tf.zeros([1,2,3])

In [ ]:
extent_lmdb.next()

In [ ]:
batch_extents_loss_mask.dtype

In [ ]:
np.exp(batch_fiducials_xy_log_var_output)

In [ ]:
output_dir

In [ ]:
graphdef = sess.graph_def
output_node_names = ['fiducials_vis_output', 'fiducials_xy_output',
                                                                            'extents_output']
frozen_graph = tf.graph_util.convert_variables_to_constants(sess, graphdef, output_node_names)
#converted_graph_def= tf.graph_util.remove_training_nodes(frozen_graph)
tf.train.write_graph(frozen_graph, "/mnt/nautilus_rw/praveen/", "pfv_model4.pb", as_text=False)

In [ ]:
batch_fiducials_vis

In [ ]:
net.fiducials_vis_loss

In [ ]:
len(last_batch_ims)

In [ ]:
extents_lmdb_paths

In [ ]:
idx = 16
ext_test_im = last_batch_ims[idx]
pred_ext, pred_ext_log_vars = sess.run([net.extents_output, net.extents_log_vars_output], {net.x: pu.normalize_ims(np.array([ext_test_im]))}) 
print pred_ext
print np.sqrt(np.exp(pred_ext_log_vars))

In [ ]:
plt.figure()
plt.imshow(ext_test_im)


In [ ]:
batch_fiducials_xy_loss_mask

In [ ]:
[(k,fiducials_dict[k]) for k in fiducials_keys]

In [ ]:
len(last_batch_ims)

In [ ]:
np.min(pu.normalize_ims(fid_test_im))

In [ ]:
idx = 22
fid_test_im = last_batch_ims[idx]
fid_test_loss_mask = batch_fiducials_xy_loss_mask[idx,:]
pred_fid_pts, pred_fid_vis, pred_extents, pred_fid_xy_log_var = (sess.run([net.fiducials_xy_output, net.fiducials_vis_output, 
                                                      net.extents_output,
                                                     net.fiducials_xy_log_vars_output], {net.x: pu.normalize_ims(np.array([fid_test_im]))}))
print 'Raw fid pts: ' + str(pred_fid_pts)
pred_fid_pts = 64 * pred_fid_pts + 32

print 'Actual fid pts: ' + str(pred_fid_pts)
gt_fids = last_batch_fid_xy * 64 + 32
print 'Extents: '
print str(pred_extents)

print 'Fiducial stdevs:'
#print str(np.exp(pred_fid_xy_log_var))
print str(np.sqrt(np.exp(pred_fid_xy_log_var) * 64 * 64))

In [ ]:
plot_fids_on_im(fid_test_im,pred_fid_pts[0,:,:])

In [ ]:
import pickle

In [ ]:
help(pickle.dump)

In [ ]:
with open('/home/praveen/test_im.pickle', 'wb') as of:
  pickle.dump(fid_test_im, of);

In [ ]:
np.max(fid_test_im)

In [ ]:
pred_fid_pts.shape

In [ ]:
pred_fid_vis

In [ ]:
np.argmax(pred_fid_vis, 2)

In [ ]:
np.argmax(pred_fid_vis, 2).shape

In [ ]:
plt.imshow(fid_test_im)

In [ ]:
batch_fiducials_vis[idx,:]

In [ ]:
batch_fiducials_xy_loss_mask

In [ ]:
pred_fid_pts

In [ ]:
gt_fids